In [1]:
import pandas as pd
import numpy as np
from scipy.linalg import sqrtm

import GPy
from scripts.process import ContactPointTracker
import plotly.graph_objects as go

%load_ext autoreload
%autoreload 2

## This Notebook is to plot and compare the performance of sensor model of Gaussian Process Regression using different kernel functions, including RBF, ThinPlate, Spline, Ploynomial, and the sensor model of the Neural Networks.

Two experiments included:

- Plot the mapping from x, y position to sensor signal with z = 0 (on the z = 0 plane), and show how the sensor signal gradients change at the edge cases.

- Compare the contact tracking performance of different models by conducting a simple sweeping trial on a 20 mm diameter cylinder.

### Experiments for the Gaussian Process Regression using different kernel functions

In [279]:
from sklearn.metrics import r2_score
import plotly.graph_objects as go

def plot_sensor_model(calibration_fn, kernel):
    data_tbl = pd.read_csv(calibration_fn)

    atten = 50
    pos_ref = np.array([[64.30451325,98.0687005,16.1023935]]) # may after new sensor stand

    P = data_tbl[['px','py','pz']].to_numpy() - pos_ref
    S = data_tbl[['sx','sy']].to_numpy()/atten

    #ker1 = GPy.kern.RBF(3, lengthscale=5, variance=10.0)
    #ker1 = GPy.kern.ThinPlate(3, variance=1, R=800)
    #ker1 = GPy.kern.Spline(3, c=5, variance=0.5)
    #ker1 = GPy.kern.Poly(3, variance=20, order=5, scale=0.05)
    mx = GPy.models.GPRegression(P,S[:,0:1],kernel)
    my = GPy.models.GPRegression(P,S[:,1:2],kernel)

    y_pred = mx.predict(P)[0]
    r2_x = r2_score(y_true = S[:,0:1], y_pred = y_pred )
    print(f'Sensor model X R2 score {r2_x}')
    y_pred = my.predict(P)[0]
    r2_y = r2_score(y_true = S[:,1:2], y_pred = y_pred )
    print(f'Sensor model Y R2 score {r2_y}')

    # get points that are near the zero plane
    select_zero_idx = np.where(np.abs(P[:,2]) < 0.001)[0]

    margin = 20
    x_range = np.arange(min(P[:,0])-margin, max(P[:,0])+margin)
    y_range = np.arange(min(P[:,1])-margin, max(P[:,1])+margin)
    [X_mesh, Y_mesh] = np.meshgrid(x_range, y_range)
    Z_mesh = np.zeros_like(X_mesh)
    points = np.vstack([X_mesh.ravel(), Y_mesh.ravel(), Z_mesh.ravel()]).T
    mx_pred = mx.predict(points)
    MX_pred = np.reshape(mx_pred[0],X_mesh.shape)
    my_pred = my.predict(points)
    MY_pred = np.reshape(my_pred[0],X_mesh.shape)
    return (X_mesh, Y_mesh, MX_pred, MY_pred)

In [3]:
from plotly.subplots import make_subplots
cmin_val = -20
cmax_val = 10
# call plot_sensor_model with the calibration file and kernel
kernel = GPy.kern.RBF(3, lengthscale=5, variance=1.0)
(X_mesh, Y_mesh, MX_pred, MY_pred) = plot_sensor_model('../data/all_datasets/calibration/tip_calib_May_04.csv', kernel)
fig = make_subplots(
    rows=1, cols=2,
    specs=[[{'type': 'surface'}, {'type': 'surface'}]])
fig.update_layout(title=f'Sensor model surface plot', 
                    title_y=0.95,
                    autosize=False,
                    scene = dict(
                        xaxis = dict(nticks=4, range=[-50,10],),
                        yaxis = dict(nticks=4, range=[-40,20],),
                        zaxis = dict(nticks=4, range=[-70,5],),),
                        #caxis = dict(range=[-10,5],),),
                    width=1400, height=700,
                    margin=dict(l=10, r=10, b=10, t=10))
fig.add_trace(go.Surface(x=X_mesh, y=Y_mesh, z=-MX_pred,cmin=cmin_val,cmax=cmax_val),col=1,row=1)
fig.add_trace(go.Surface(x=X_mesh, y=Y_mesh, z=-MY_pred,cmin=cmin_val,cmax=cmax_val),col=2,row=1)
fig.show()

# call plot_sensor_model with the calibration file and kernel
kernel = GPy.kern.Poly(3, variance=1, order=5, scale=0.05)
(X_mesh, Y_mesh, MX_pred, MY_pred) = plot_sensor_model('../data/all_datasets/calibration/tip_calib_May_04.csv', kernel)
fig = make_subplots(
    rows=1, cols=2,
    specs=[[{'type': 'surface'}, {'type': 'surface'}]])
fig.update_layout(title=f'Sensor model surface plot', 
                    title_y=0.95,
                    autosize=False,
                    scene = dict(
                        xaxis = dict(nticks=4, range=[-50,10],),
                        yaxis = dict(nticks=4, range=[-40,20],),
                        zaxis = dict(nticks=4, range=[-70,5],),),
                    width=1400, height=700,
                    margin=dict(l=10, r=10, b=10, t=10))
fig.add_trace(go.Surface(x=X_mesh, y=Y_mesh, z=-MX_pred,cmin=cmin_val,cmax=cmax_val),col=1,row=1)
fig.add_trace(go.Surface(x=X_mesh, y=Y_mesh, z=-MY_pred,cmin=cmin_val,cmax=cmax_val),col=2,row=1)
fig.show()

# call plot_sensor_model with the calibration file and kernel
kernel = GPy.kern.Poly(3, variance=1, order=4, scale=0.05)
(X_mesh, Y_mesh, MX_pred, MY_pred) = plot_sensor_model('../data/all_datasets/calibration/tip_calib_May_04.csv', kernel)
fig = make_subplots(
    rows=1, cols=2,
    specs=[[{'type': 'surface'}, {'type': 'surface'}]])
fig.update_layout(title=f'Sensor model surface plot', 
                    title_y=0.95,
                    autosize=False,
                    scene = dict(
                        xaxis = dict(nticks=4, range=[-50,10],),
                        yaxis = dict(nticks=4, range=[-40,20],),
                        zaxis = dict(nticks=4, range=[-70,5],),),
                    width=1400, height=700,
                    margin=dict(l=10, r=10, b=10, t=10))
                    
fig.add_trace(go.Surface(x=X_mesh, y=Y_mesh, z=-MX_pred,cmin=cmin_val,cmax=cmax_val),col=1,row=1)
fig.add_trace(go.Surface(x=X_mesh, y=Y_mesh, z=-MY_pred,cmin=cmin_val,cmax=cmax_val),col=2,row=1)
fig.show()

# call plot_sensor_model with the calibration file and kernel
kernel = GPy.kern.Poly(3, variance=1, order=5, scale=0.05)
(X_mesh, Y_mesh, MX_pred, MY_pred) = plot_sensor_model('../data/all_datasets/calibration/tip_calib_May_04.csv', kernel)
fig = make_subplots(
    rows=1, cols=2,
    specs=[[{'type': 'surface'}, {'type': 'surface'}]])

fig.update_layout(title=f'Sensor model surface plot', 
                    title_y=0.95,
                    autosize=False,
                    scene = dict(
                        xaxis = dict(nticks=4, range=[-50,10],),
                        yaxis = dict(nticks=4, range=[-40,20],),
                        zaxis = dict(nticks=4, range=[-70,5],),),
                    width=1400, height=700,
                    margin=dict(l=10, r=10, b=10, t=10))
                    
fig.add_trace(go.Surface(x=X_mesh, y=Y_mesh, z=-MX_pred,cmin=cmin_val,cmax=cmax_val),col=1,row=1)
fig.add_trace(go.Surface(x=X_mesh, y=Y_mesh, z=-MY_pred,cmin=cmin_val,cmax=cmax_val),col=2,row=1)

# update figure layout and limit z axis


fig.show()

Sensor model X R2 score 0.992163210003221
Sensor model Y R2 score 0.992578138589828


Sensor model X R2 score 0.9976712212711681
Sensor model Y R2 score 0.9966552255439372


Sensor model X R2 score 0.9944379832102591
Sensor model Y R2 score 0.9928092046604866


Sensor model X R2 score 0.9976712212711681
Sensor model Y R2 score 0.9966552255439372


In [29]:
sensor_data = np.load('../data/sensor_models/sensor1/sensor1_models.npz', allow_pickle=True)#['data_dict'].item()
sensor_shape_arr = sensor_data['shape']

In [6]:
# call plot_sensor_model with the calibration file and kernel
kernel = GPy.kern.Poly(3, variance=1, order=4, scale=0.05)
(X_mesh, Y_mesh, MX_pred, MY_pred) = plot_sensor_model('../data/all_datasets/calibration/tip_calib_May_04.csv', kernel)
fig = go.Figure()
fig.add_trace(go.Surface(x=X_mesh, y=Y_mesh, z=-MX_pred,cmin=cmin_val,cmax=cmax_val))
fig.add_trace(go.Scatter3d(x=sensor_shape_arr[:,0], y=sensor_shape_arr[:,1], z=sensor_shape_arr[:,2], mode='lines', line=dict(color='royalblue', width=4, dash='dot')))
fig.update_layout(title=f'Sensor model surface plot', 
                    title_y=0.95,
                    autosize=True,
                    scene = dict(
                        xaxis = dict(nticks=4, range=[-50,10],),
                        yaxis = dict(nticks=4, range=[-40,20],),
                        zaxis = dict(nticks=4, range=[-50,5],),),
                    width=1000, height=700,
                    margin=dict(l=10, r=10, b=10, t=10))
fig.show()
fig = go.Figure()
fig.add_trace(go.Surface(x=X_mesh, y=Y_mesh, z=-MY_pred,cmin=cmin_val,cmax=cmax_val))
fig.add_trace(go.Scatter3d(x=sensor_shape_arr[:,0], y=sensor_shape_arr[:,1], z=sensor_shape_arr[:,2], mode='lines', line=dict(color='royalblue', width=4, dash='dot')))
fig.update_layout(title=f'Sensor model surface plot', 
                    title_y=0.95,
                    autosize=True,
                    scene = dict(
                        xaxis = dict(nticks=4, range=[-50,10],),
                        yaxis = dict(nticks=4, range=[-40,20],),
                        zaxis = dict(nticks=4, range=[-50,5],),),
                    width=1000, height=700,
                    margin=dict(l=10, r=10, b=10, t=10))
fig.show()

Sensor model X R2 score 0.9944379832102591
Sensor model Y R2 score 0.9928092046604866


In [285]:

# call plot_sensor_model with the calibration file and kernel
kernel = GPy.kern.ThinPlate(3, variance=1.0, R=1000)
(X_mesh, Y_mesh, MX_pred, MY_pred) = plot_sensor_model('../data/all_datasets/calibration/tip_calib_May_04.csv', kernel)
cmin_val = -20
cmax_val = 10

fig = make_subplots(
    rows=1, cols=2,
    specs=[[{'type': 'surface'}, {'type': 'surface'}]])

fig.update_layout(title=f'ThinPlate Sensor model surface plot', 
                    title_y=0.95,
                    autosize=False,
                    scene = dict(
                        xaxis = dict(nticks=4, range=[-50,10],),
                        yaxis = dict(nticks=4, range=[-40,20],),
                        zaxis = dict(nticks=4, range=[-70,15],),),
                        #caxis = dict(range=[-10,5],),),
                    width=1400, height=700,
                    margin=dict(l=10, r=10, b=10, t=10))

fig.add_trace(go.Surface(x=X_mesh, y=Y_mesh, z=-MX_pred,cmin=cmin_val,cmax=cmax_val),col=1,row=1)
fig.add_trace(go.Scatter3d(x=sensor_shape_arr[:,0], y=sensor_shape_arr[:,1], z=sensor_shape_arr[:,2], mode='lines', line=dict(color='royalblue', width=4, dash='dot')), col=1, row=1)
fig.add_trace(go.Surface(x=X_mesh, y=Y_mesh, z=-MY_pred,cmin=cmin_val,cmax=cmax_val),col=2,row=1)
fig.add_trace(go.Scatter3d(x=sensor_shape_arr[:,0], y=sensor_shape_arr[:,1], z=sensor_shape_arr[:,2], mode='lines', line=dict(color='royalblue', width=4, dash='dot')), col=2, row=1)
fig.show()

Sensor model X R2 score 0.9998151731366404
Sensor model Y R2 score 0.9996898616439036


In [300]:
## Testing tracking with 30 mm cylinder

import plotly.graph_objects as go

#kern = GPy.kern.Poly(3, variance=1.0, order=5, scale=0.1)
#kern = GPy.kern.RBF(3, lengthscale=5, variance=10.0)
kern = GPy.kern.ThinPlate(3, variance=1.0, R=1000)

fig = go.Figure()

for i in range(1,5):
    #tracker = ContactPointTracker(fm_alpha=1.2, sigma_process_init=0.2, mu0=np.array([-10,-20,0]))
    # tracker = ContactPointTracker(fm_alpha=1.25, fm_stride=1,
    #                               sigma_process_init=0.2, mu0=np.array([-5,-5,0]))
    tracker = ContactPointTracker(fm_alpha=1.25, sigma_process_init=0.2,  mu0=np.array([-10,-20,0]))
    tracker.init_calibration_model(calibration_fn='../data/all_datasets/calibration/tip_calib_May_04.csv',
                                input_ref=np.array([[64.30451325,98.0687005,16.1023935]]),
                                kernel=kern)

    tracker.initialize(track_data_fn=f'../data/all_datasets/test/tip_test_05_09_23/tip_test_cylinder_30mm_May_09_trial{i}.csv',
                                offset_mode='from_data')

    x_ukf, sig_ukf, additional_data = tracker.run_tracker(track_mode='static')

    x_est = x_ukf.T
    x_err = additional_data['X_t']-x_est

    selection_arr_np = np.where(np.array(additional_data['selection_arr']))[0]
    x_err_sel = x_err[selection_arr_np,:]

    sig_ukf_sel = sig_ukf[:,:,selection_arr_np]

    ev_array = np.zeros(sig_ukf_sel.shape[2])

    for i in range(sig_ukf_sel.shape[2]):
        ev_array[i] = np.linalg.eig(sig_ukf_sel[:,:,i])[0][1]
    #x_err = x_err[np.where(ev_array < .005)[0],:]
    #x_err_filt = x_err_sel[np.where(ev_array < 1)[0],:]

    fig.add_trace(go.Scatter(x=x_err_sel[10:,0], y=x_err_sel[10:,1],
                        name='lines'))

c_pos = np.array([0,12])
c_rad = 15
fig.add_shape(type="circle",
    xref="x", yref="y",
    x0=c_pos[0]-c_rad, y0=c_pos[1]-c_rad, x1=c_pos[0]+c_rad, y1=c_pos[1]+c_rad,
    line=dict(width=1),
    fillcolor="PaleTurquoise",
    opacity=0.3
)

camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=0, y=0, z=0),
    eye=dict(x=0, y=0, z=2.25)
)
fig.update_layout(title='3D Localization', 
				scene = dict(
					xaxis = dict(nticks=4, range=[-15,5],),
                    yaxis = dict(nticks=4, range=[-5,15],),
                    zaxis = dict(nticks=4, range=[-40,40],),),
				xaxis_title='x axis (mm)', yaxis_title='y axis (mm)',
				autosize=False,
				width=500, height=500,
				scene_camera=camera,
				margin=dict(l=10, r=10, b=10, t=50))

fig.update_yaxes(
    scaleanchor="x",
    scaleratio=1,
    range=[-10,40]
  )


fig.show()

In [8]:
## Testing tracking with 20 mm cylinder

import plotly.graph_objects as go

kern = GPy.kern.Poly(3, variance=1.0, order=3, scale=0.1)
#kern = GPy.kern.RBF(3, lengthscale=5, variance=1.0)
#kern = GPy.kern.ThinPlate(3, variance=1.0, R=100)

fig = go.Figure()

c_pos = np.array([0,12])
c_rad = 10
fig.add_shape(type="circle",
    xref="x", yref="y",
    x0=c_pos[0]-c_rad, y0=c_pos[1]-c_rad, x1=c_pos[0]+c_rad, y1=c_pos[1]+c_rad,
    line=dict(width=1),
    fillcolor="PaleTurquoise",
    opacity=0.3
)

for i in range(6,10):
    tracker = ContactPointTracker(fm_alpha=1.2, fm_stride=1,
                                  sigma_process_init=10., mu0=np.array([-5, -15, 0]))
    #tracker = ContactPointTracker(fm_alpha=1.05, sigma_process_init=10)
    tracker.init_calibration_model(calibration_fn='../data/all_datasets/calibration/tip_calib_May_04.csv',
                                input_ref=np.array([[64.30451325,98.0687005,16.1023935]]),
                                kernel=kern)

    tracker.initialize(track_data_fn=f'../data/all_datasets/test/tip_test_05_09_23/tip_test_cylinder_30mm_May_09_trial{i}.csv',
                                offset_mode='from_data')

    x_ukf, sig_ukf, additional_data = tracker.run_tracker(track_mode='static')

    x_est = x_ukf.T
    x_err = additional_data['X_t']-x_est

    selection_arr_np = np.where(np.array(additional_data['selection_arr']))[0]
    x_err_sel = x_err[selection_arr_np,:]

    sig_ukf_sel = sig_ukf[:,:,selection_arr_np]

    ev_array = np.zeros(sig_ukf_sel.shape[2])

    for i in range(sig_ukf_sel.shape[2]):
        ev_array[i] = np.linalg.eig(sig_ukf_sel[:,:,i])[0][1]
    #x_err = x_err[np.where(ev_array < .005)[0],:]
    #x_err_filt = x_err_sel[np.where(ev_array < 1)[0],:]

    fig.add_trace(go.Scatter(x=x_err_sel[10:,0], y=x_err_sel[10:,1],
                        name='lines'))


camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=0, y=0, z=0),
    eye=dict(x=0, y=0, z=2.25)
)
fig.update_layout(title='3D Localization', 
				scene = dict(
					xaxis = dict(nticks=4, range=[-15,5],),
                    yaxis = dict(nticks=4, range=[-5,15],),
                    zaxis = dict(nticks=4, range=[-40,40],),),
				xaxis_title='x axis (mm)', yaxis_title='y axis (mm)',
				autosize=False,
				width=500, height=500,
				scene_camera=camera,
				margin=dict(l=10, r=10, b=10, t=50))

fig.update_yaxes(
    scaleanchor="x",
    scaleratio=1,
    range=[0,40]
  )


fig.show()

### Experiments for the Neural Network model

Details for the NN model:

- Please refer to the model.py for the model architecture
- Dataset Split:
    - 8 sensors data for training (#8, #9, #10, #11, #12, #13, #15, #16)
    - 3 sensors data for testing (#1, #4, #5)
- Parameters:
    - 50 epochs
    - 0.001 learning rate
- Model is selected based on tracking performance.
    - training error: 0.004973
    - testing error: 0.004825

#### Plot the mapping from contact position to sensor signal on the z=0 plane

In [54]:
from sklearn.metrics import r2_score
import plotly.graph_objects as go
from scipy.interpolate import splrep, BSpline
from scripts.model import DLSensorModel
import torch

def plot_sensor_model(calib_pth, shape_x_pth, shape_y_pth, model_pth, pos_ch=1, shape_ch=11, atten = 50, pos_ref = np.array([[64.30451325,98.0687005,16.1023935]])):
    # set device to M1 GPU
    device = torch.device("mps")
    
    # load calibration data collected for the testing sensor
    calib_data = pd.read_csv(calib_pth)
    P = calib_data[['px','py','pz']].to_numpy() - pos_ref
    P_tensor = np.expand_dims(P, axis=1)
    P_tensor = torch.from_numpy(P_tensor).type(torch.FloatTensor).to(device)
    S = calib_data[['sx','sy']].to_numpy()
    max_s = S.max()
    min_s = S.min()
    
    # load sensor shape matrix
    shape_x = pd.read_csv(shape_x_pth)
    pts_x = shape_x[['px']].to_numpy()[:,0]
    pts_z = shape_x[['pz']].to_numpy()[:,0]
    shape_y = pd.read_csv(shape_y_pth)
    pts_x_new = shape_y[['px']].to_numpy()[:,0]
    pts_y = shape_y[['py']].to_numpy()[:,0]
    m_shape = BSpline(*splrep(x=pts_x[::-1], y=pts_z[::-1], s=2))
    X = pts_x_new - pts_x_new[0]
    Y = pts_y - pts_y[0]
    Z = m_shape(pts_x_new) - m_shape(pts_x_new)[0]
    shape_numpy = np.vstack((X, Y, Z)).T

    
    # load trained model
    model = DLSensorModel(pos_ch, shape_ch)
    model.load_state_dict(torch.load(model_pth))
    model.to(device)
    model.eval()
    
    shape_matrix = np.repeat(np.expand_dims(shape_numpy, axis=0), P.shape[0], axis=0)
    shape_matrix = torch.from_numpy(shape_matrix).type(torch.FloatTensor).to(device)
    pred = model(P_tensor, shape_matrix).cpu().detach().numpy()
    pred = pred * (max_s - min_s) + min_s
    r2_x = r2_score(y_true = S[:,0:1], y_pred = pred[:,0])
    print(f'Sensor model X R2 score {r2_x}')
    r2_y = r2_score(y_true = S[:,1:2], y_pred = pred[:,1])
    print(f'Sensor model Y R2 score {r2_y}')

    # Get data at z=zero plane
    margin = 20
    x_range = np.arange(min(P[:,0])-margin, max(P[:,0])+margin)
    y_range = np.arange(min(P[:,1])-margin, max(P[:,1])+margin)
    [X_mesh, Y_mesh] = np.meshgrid(x_range, y_range)
    Z_mesh = np.zeros_like(X_mesh)
    points = np.vstack([X_mesh.ravel(), Y_mesh.ravel(), Z_mesh.ravel()]).T
    points_tensor = torch.from_numpy(np.expand_dims(points, axis=1)).type(torch.FloatTensor).to(device)
    shape_matrix = np.repeat(np.expand_dims(shape_numpy, axis=0), points.shape[0], axis=0)
    shape_matrix = torch.from_numpy(shape_matrix).type(torch.FloatTensor).to(device)
    pred = model(points_tensor, shape_matrix).cpu().detach().numpy()
    pred = pred * (max_s - min_s) + min_s
    pred /= atten
    MX_pred = np.reshape(pred[:, 0], X_mesh.shape)
    MY_pred = np.reshape(pred[:, 1], X_mesh.shape)
    return (X_mesh, Y_mesh, MX_pred, MY_pred, shape_numpy)

In [277]:
from plotly.subplots import make_subplots
cmin_val = -20
cmax_val = 10
# call plot_sensor_model with the calibration file and kernel
calib_pth = '../data/all_datasets/calibration/tip_calib_May_04.csv'
shape_x_pth = '../data/all_datasets/shape/sensor1_tip_shape_x_May_17_less.csv'
shape_y_pth = '../data/all_datasets/shape/sensor1_tip_shape_y_May_17_less.csv'
model_pth = 'scripts/saved_model/ep20.pth'
(X_mesh, Y_mesh, MX_pred, MY_pred, sensor_shape_arr) = plot_sensor_model(calib_pth, shape_x_pth, shape_y_pth, model_pth, pos_ref=np.array([64.30451325,98.0687005,16.1023935]))
fig = make_subplots(
    rows=1, cols=2,
    specs=[[{'type': 'surface'}, {'type': 'surface'}]])

fig.update_layout(title=f'DL Sensor model surface plot', 
                    title_y=0.95,
                    autosize=False,
                    scene = dict(
                        xaxis = dict(nticks=4, range=[-50,10],),
                        yaxis = dict(nticks=4, range=[-40,20],),
                        zaxis = dict(nticks=4, range=[-70,15],),),
                        #caxis = dict(range=[-10,5],),),
                    width=1400, height=700,
                    margin=dict(l=10, r=10, b=10, t=10))
fig.add_trace(go.Surface(x=X_mesh, y=Y_mesh, z=-MX_pred,cmin=cmin_val,cmax=cmax_val),col=1,row=1)
fig.add_trace(go.Scatter3d(x=sensor_shape_arr[:,0], y=sensor_shape_arr[:,1], z=sensor_shape_arr[:,2], mode='lines', line=dict(color='royalblue', width=4, dash='dot')), col=1, row=1)
fig.add_trace(go.Surface(x=X_mesh, y=Y_mesh, z=-MY_pred,cmin=cmin_val,cmax=cmax_val),col=2,row=1)
fig.add_trace(go.Scatter3d(x=sensor_shape_arr[:,0], y=sensor_shape_arr[:,1], z=sensor_shape_arr[:,2], mode='lines', line=dict(color='royalblue', width=4, dash='dot')), col=2, row=1)
fig.show()

Sensor model X R2 score 0.9719176609627198
Sensor model Y R2 score 0.9527446648952418


#### Experiments of tracking a static point

See NoiseToRobotProprio.ipynb for the details of this experiment

In [160]:
from scripts.process import ContactPointTracker
import plotly.graph_objects as go
import os
import seaborn as sns
import yaml

def aggregate_error_data(trial_files, cfg_dict, input_ref, err_len, init_pos_offset=np.array([5,5,0]), sensor_atten=100, signal_threshold = 5):  
    """ Aggregate error of all trials (10), put them in one variable
    
    Args:
        - trial_files: list of csv file of trajectories of all trials
        - calibration_file: calibration data for the selected sensor (semi-curved, curved, straight)
        - input_ref: reference origin of the sensor base (measured)
        - err_len: selected number of timesteps (iterations) to plot (used to see how long it converges)
        - init_pos_offset: offset position added to all the points
        - sensor_atten: scaling factor to scale down raw sensor values
    """  
    all_error_data = pd.DataFrame(columns=['x','norm_err'])
    for file in trial_files:
        tracker = ContactPointTracker(fm_alpha= 1.04,
                                    sigma_process=1e-5, 
                                    sigma_process_init=10., 
                                    sigma_sensor=0.01)
        tracker.init_DL_model(cfg_dict)
        
        tracker.initialize(track_data_fn=file,
                                input_ref=input_ref, 
                                sensor_atten=sensor_atten,
                                signal_threshold=signal_threshold
                                )
        x_ukf, sig_ukf, additional_data = tracker.run_tracker(track_mode='world',init_pos_offset=init_pos_offset)

        x_est = x_ukf.T
        x_err = additional_data['X_t']-x_est

        selection_arr_np = np.where(np.array(additional_data['selection_arr']) == 1)[0]

        norm_err = np.linalg.norm(x_err[selection_arr_np,:], axis=1)
        if norm_err.shape[0] != 0:
            x = np.arange(err_len)
            norm_arr = np.column_stack((x,norm_err[:err_len]))
            all_error_data = pd.concat([all_error_data, pd.DataFrame(norm_arr, columns=['x','norm_err'])])
        
    return all_error_data

def plot_error_data(all_error_data, title="Error"):
    """ Calculate the mean error along all trials and plot them with confidence intervals

    Args:
        all_error_data (array): aggregated error along all trials
        title (str, optional): title. Defaults to "Error".

    Returns:
        _type_: _description_
    """
    # calculate mean and std of error for each trial
    mean_err = all_error_data.groupby('x').mean()
    std_err = all_error_data.groupby('x').sem()
    ci_lower = mean_err['norm_err'] - 1.96 * std_err['norm_err']
    ci_upper = mean_err['norm_err'] + 1.96 * std_err['norm_err']
    overall_mean = mean_err['norm_err'].mean()
    overall_std = mean_err['norm_err'].sem()
    
    # max and min error and convergence time
    sample_rate = 200 # Hz
    max_error = all_error_data.groupby('x').max()['norm_err'].max()
    min_error = all_error_data.groupby('x').min()['norm_err'].min()
    conv_idx = np.where(mean_err['norm_err'].to_numpy() < 1)[0]
    if len(conv_idx) != 0:
        conv_idx = conv_idx[0]
    else:
        conv_idx = -100
    conv_time = conv_idx * 1 / sample_rate # seconds

    ### Seaborn method
    # sns.lineplot(data=all_error_data, x="x", y="norm_err", orient="x", errorbar="ci")

    fig = go.Figure([
        go.Scatter(
            name='Avg Error (mm)',
            x=all_error_data['x'],
            y=all_error_data.groupby('x').mean()['norm_err'],
            mode='lines',
            line=dict(color='rgb(31, 119, 180)'),
        ),
        go.Scatter(
            name='95% CI Upper',
            x=all_error_data['x'],
            # y=all_error_data.groupby('x').max()['norm_err'],
            y = ci_upper[:, ],
            mode='lines',
            marker=dict(color='#444'),
            line=dict(width=0),
            showlegend=False
        ),
        go.Scatter(
            name='95% CI Lower',
            x=all_error_data['x'],
            # y=all_error_data.groupby('x').min()['norm_err'],
            y = ci_lower[:, ],
            marker=dict(color='#444'),
            line=dict(width=0),
            mode='lines',
            fillcolor='rgba(68, 68, 68, 0.3)',
            fill='tonexty',
            showlegend=False
        )
    ])
    
    if conv_idx > 0:
        fig.add_annotation(x = conv_idx, 
                        y = mean_err['norm_err'].to_numpy()[conv_idx], 
                        text= "Convergence Time (seconds): " + "%.3f" % conv_time,
                        showarrow=True,
                        arrowhead=1
                        )
    fig.update_layout(
        yaxis_title='Avg Error',
        title="Mean: " + "%.3f" % overall_mean + " SD: " + "%.3f" % overall_std + ' Max: ' + "%.3f" % max_error + ' Min: ' + "%.3f" % min_error,
        hovermode='x'
    )
    fig.update_layout(width=int(650), showlegend=False)
    return fig

In [273]:
sensor_atten=50
signal_threshold = 250 / sensor_atten
input_ref=np.array([[64.30451325,98.0687005,16.1023935]])
cfg_pth = "scripts/config/test.yaml"
with open(cfg_pth, "r") as f:
    cfg_dict = yaml.load(f, Loader=yaml.FullLoader)

directory = '../data/all_datasets/test/tip_test_05_24_23/'
file_list = [os.path.join(directory, f) for f in os.listdir(directory) if f.endswith('.csv') and f.startswith('tip')]
all_error_data_tip = aggregate_error_data(file_list[:], \
                        cfg_dict, input_ref=input_ref, err_len=54, 
                        init_pos_offset=np.array([10,0,0]),
                        sensor_atten=sensor_atten,
                        signal_threshold = signal_threshold)

fig = plot_error_data(all_error_data_tip, title="Tracking Error Sensor H")
fig.update_xaxes(title_text='Time (iterations)')
fig.show()

/var/folders/_6/_z3nbpv93c31_kcf1k1_51mm0000gn/T/ipykernel_11980/1700672756.py:42: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.



#### Experiments of sweeping on a 30 mm diameter 

In [274]:
## Testing tracking with 30 mm cylinder
import plotly.graph_objects as go
fig = go.Figure()

sensor_atten=50
signal_threshold = 250 / sensor_atten
input_ref=np.array([[64.30451325,98.0687005,16.1023935]])

cfg_pth = "scripts/config/test.yaml"
with open(cfg_pth, "r") as f:
    cfg_dict = yaml.load(f, Loader=yaml.FullLoader)

for i in range(1,5):
    tracker = ContactPointTracker(fm_alpha=1.25,
                                    fm_stride=1,
                                    sigma_process=1e-5, 
                                    sigma_process_init=10, 
                                    sigma_sensor=0.01,
                                    mu0=np.array([-10,-20,0]))
    tracker.init_DL_model(cfg_dict)

    tracker.initialize(track_data_fn=f'../data/all_datasets/test/tip_test_05_09_23/tip_test_cylinder_30mm_May_09_trial{i}.csv',
                        sensor_atten=sensor_atten,
                        offset_mode='from_data',
                        signal_threshold=signal_threshold)

    x_ukf, sig_ukf, additional_data = tracker.run_tracker(track_mode='static')

    x_est = x_ukf.T
    x_err = additional_data['X_t']-x_est

    selection_arr_np = np.where(np.array(additional_data['selection_arr']))[0]
    x_err_sel = x_err[selection_arr_np,:]

    sig_ukf_sel = sig_ukf[:,:,selection_arr_np]

    ev_array = np.zeros(sig_ukf_sel.shape[2])

    for i in range(sig_ukf_sel.shape[2]):
        ev_array[i] = np.linalg.eig(sig_ukf_sel[:,:,i])[0][1]

    fig.add_trace(go.Scatter(x=x_err_sel[10:,0], y=x_err_sel[10:,1],
                        name='lines'))

c_pos = np.array([0,12])
c_rad = 15
fig.add_shape(type="circle",
    xref="x", yref="y",
    x0=c_pos[0]-c_rad, y0=c_pos[1]-c_rad, x1=c_pos[0]+c_rad, y1=c_pos[1]+c_rad,
    line=dict(width=1),
    fillcolor="PaleTurquoise",
    opacity=0.3
)

camera = dict(
    up=dict(x=0, y=0, z=1),
    center=dict(x=0, y=0, z=0),
    eye=dict(x=0, y=0, z=2.25)
)
fig.update_layout(title='3D Localization', 
				scene = dict(
					xaxis = dict(nticks=4, range=[-15,5],),
                    yaxis = dict(nticks=4, range=[-5,15],),
                    zaxis = dict(nticks=4, range=[-40,40],),),
				xaxis_title='x axis (mm)', yaxis_title='y axis (mm)',
				autosize=False,
				width=500, height=500,
				scene_camera=camera,
				margin=dict(l=10, r=10, b=10, t=50))

fig.update_yaxes(
    scaleanchor="x",
    scaleratio=1,
    range=[-10,40]
  )


fig.show()